In [14]:
import xml.etree.cElementTree as et
import pandas as pd
from sqlalchemy import create_engine
import os
import sys


In [15]:
##TODO:set the location of the wcproduction.xml file and the dbname to output.
sourceXML="K:/hbarrett/wcproduction.xml"
dbname = "ocd.db"
#this is how many to process before inserting into the db
iterate_amount=1000

def extract_local_tag(qname):
    '''extracts and returns just the local tag for an element.'''
    return qname.split('}')[-1]

def save_oil_records(fulldf,db_engine):
    fulldf[["api_st_cde","api_cnty_cde","api_well_idn","pool_idn","prodn_mth","prodn_yr","ogrid_cde","prod_amt","prodn_day_num"]] = fulldf[["api_st_cde","api_cnty_cde","api_well_idn","pool_idn","prodn_mth","prodn_yr","ogrid_cde","prod_amt","prodn_day_num"]].apply(pd.to_numeric)
    fulldf[["eff_dte","mod_dte"]] = fulldf[["eff_dte","mod_dte"]].apply(pd.to_datetime)
    fulldf.to_sql('oil_log', db_engine, if_exists='append')
    new_empty_df = pd.DataFrame()
    return new_empty_df

if os.path.exists(dbname):
    print("Deleting "+dbname+" database.")
    os.remove(dbname)

#Create a sqlite sqlalchemy db connection.
disk_engine = create_engine('sqlite:///'+ dbname)

#idx is the index for every record we will insert.
idx=0

#count is used to iterate n number of records before we insert.
count=0

#This is the schema tag we want to ignore.
ixid_uri = 'urn:schemas-microsoft-com:sql:SqlRowSet1'

#Create empty Data frame.
fulldf = pd.DataFrame()

#Open the xmlfile...
with open(sourceXML) as xml_file:
    #For each element...
    for event, elem in et.iterparse(xml_file):
        #if the element tag is 'wcproduction'...
        if elem.tag == et.QName(ixid_uri, 'wcproduction'):
            #create and populate a dictionary with the tag name and content of each chiled element in wcproduction
            #Example:{'eff_dte': '1973-10-31T00:00:00', 'prodn_day_num': '99', 'amend_ind': 'N', 'c115_wc_stat_cde': 'P', 'mod_dte': '2015-04-07T07:31:29.370', 'prod_amt': '91847', 'api_well_idn': '5250', 'pool_idn': '28509', 'ogrid_cde': '21075', 'api_cnty_cde': '15', 'prodn_yr': '1973', 'prodn_mth': '10', 'prd_knd_cde': 'O', 'api_st_cde': '30'}
            d = {}
            for child in elem:
                tagname=extract_local_tag(child.tag)
                d[tagname] = child.text.strip()
            #Add new dictionary to a temporary dataframe with the current index.
            dftmp=pd.DataFrame(d,index=[idx])
            #Append this dataframe to the full dataframe.
            fulldf=fulldf.append(dftmp)
            #If we have enough to insert, insert them and set count to 0.
            if count==iterate_amount:
                fulldf=save_oil_records(fulldf,disk_engine)
                count=0
                print(str(idx)+" records inserted")
            #Otherwise, just increment the index and the count.
            idx=idx+1
            count=count+1
    #if the for loop has finished, and there are still records to be processed, (count is something other than 0), then we insert the last records, and finish the bar.
    if count>0:
        fulldf=save_oil_records(fulldf,disk_engine)
        count=0
        print(str(idx)+" records inserted")


Deleting ocd2db database.
251 records inserted
